In [11]:
import sys
import os
sys.path.append('../preprocessing/')

import warnings
warnings.filterwarnings("ignore")

import pandas as pd
import numpy as np
from preprocess import *
from shallow_learning import *

import numpy as np
from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.model_selection import ParameterGrid
import time
from gensim.models import Word2Vec
from nltk.tokenize import word_tokenize
import random

np.random.seed(42)
random.seed(42)

def optimize_vectorization(df_name, df, column, target, param_grid, algorithm='tfidf', sample_size=15000):

    def evaluate_vectorization(vectors):
        similarities = cosine_similarity(vectors)
        avg_similarity = np.mean(similarities)
        return avg_similarity  # The lower the average similarity, the better the separation between documents

    # Checks if the file "Results.csv" exists
    if os.path.isfile("Results.csv"):#("Results.csv"):
        print("The file 'Results.csv' exists in the folder, loading data...")
        df_results = pd.read_csv('Results.csv')
    else:
        print("The file 'Results.csv' does not exist in the folder, creating the file...")
        df_results = pd.DataFrame(columns=["dataset", "vectorization", "params", "best_model_name", "accuracy_test", "f1_test", "score_similarity"])
        df_results.to_csv("Results.csv", index=False)
        
    # Verify the size of the dataset and sample if necessary
    is_large_dataset = len(df) > sample_size
    if is_large_dataset:
        print(f"Dataset is too large ({len(df)} instances). Sampling {sample_size} instances.")
        sampled_data = df.sample(sample_size, random_state=42)
    else:
        sampled_data = df

    # Initialize variables to store progress
    best_score = -np.inf
    best_similarity = -np.inf
    best_params = None
    best_model = None

    # If the dataset is small, start with the default vectorizer
    if not is_large_dataset:
        print(f"\nDataset small. Initiating with {algorithm} default.")
        
        if algorithm == 'tfidf':
            vectorizer = TfidfVectorizer()
            term_matrix = vectorizer.fit_transform(sampled_data[column])
            score_similarity = evaluate_vectorization(term_matrix.toarray())
            term_matrix = pd.DataFrame.sparse.from_spmatrix(term_matrix)
            term_matrix.columns = vectorizer.get_feature_names_out()
            term_matrix = pd.concat([term_matrix, df[target].reset_index(drop=True)], axis=1)
        elif algorithm == 'bow':
            vectorizer = CountVectorizer()
            term_matrix = vectorizer.fit_transform(sampled_data[column])
            score_similarity = evaluate_vectorization(term_matrix.toarray())
            term_matrix = pd.DataFrame.sparse.from_spmatrix(term_matrix)
            term_matrix.columns = vectorizer.get_feature_names_out()
            term_matrix = pd.concat([term_matrix, df[target].reset_index(drop=True)], axis=1)
        else: 
            term_matrix = tokenize(sampled_data)
            params = {'corpus_file':None, 'vector_size':100, 'alpha':0.025, 
                      'window':5, 'min_count':5, 'max_vocab_size':None, 'sample':0.001, 'seed':1, 
                      'workers':1, 'min_alpha':0.0001, 'sg':0, 'hs':0, 'negative':5, 'ns_exponent':0.75, 
                      'cbow_mean':1, 'epochs':5, 'null_word':0, 'trim_rule':None, 'sorted_vocab':1, 
                      'batch_words':10000, 'compute_loss':False, 'callbacks':(), 'comment':None, 
                      'max_final_vocab':None, 'shrink_windows':True}
            vectorizer = Word2Vec(term_matrix['tokens'], **params)
            term_matrix['word2vec_features'] = term_matrix['tokens'].apply(get_word2vec_features, args=(vectorizer,))
            term_matrix = pd.DataFrame(term_matrix['word2vec_features'].tolist())
            term_matrix.columns = term_matrix.columns.astype(str)
            term_matrix.fillna(0, inplace=True)
            score_similarity = evaluate_vectorization(term_matrix.to_numpy())
            term_matrix = pd.concat([term_matrix, df[target].reset_index(drop=True)], axis=1)

        X_train, X_test, y_train, y_test = split(term_matrix, target=target)

        # Run training with predefined parameters and multiple metrics
        best_algorithm, model, score = training_model(X_train, X_test, y_train, y_test, 
                                                    algorithms=['rf', 'svm', 'nb', 'lr'], verbose=1)

        best_similarity = score_similarity
        best_model = model
        best_score = score
        if algorithm != 'word2vec':
            best_params = vectorizer.get_params()
        else: 
            best_params = params
            
        print(f"Initial score: {best_score:.4f}")
        print(f"Initial similarity: {score_similarity:.4f}")

        # Saving the results in the DataFrame
        y_pred = model.predict(X_test)
        accuracy = accuracy_score(y_test, y_pred)
        new_data = [df_name, algorithm, best_params, best_algorithm, accuracy, score, score_similarity]
        df_results.loc[len(df_results)] = new_data

    # Iterate over the combinations of parameters for grid search
    total_combinations = len(ParameterGrid(param_grid))
    start_time = time.time()

    for idx, params in enumerate(ParameterGrid(param_grid), 1):
        print(f"\n[{idx}/{total_combinations}] Testing parameters: {params}")

        if algorithm == 'tfidf':
            vectorizer = TfidfVectorizer(**params)
            term_matrix = vectorizer.fit_transform(sampled_data[column])
            score_similarity = evaluate_vectorization(term_matrix.toarray())
            term_matrix = pd.DataFrame.sparse.from_spmatrix(term_matrix)
            term_matrix.columns = vectorizer.get_feature_names_out()
            term_matrix = pd.concat([term_matrix, df[target].reset_index(drop=True)], axis=1)
        elif algorithm == 'bow':
            vectorizer = CountVectorizer(**params)
            term_matrix = vectorizer.fit_transform(sampled_data[column])
            score_similarity = evaluate_vectorization(term_matrix.toarray())
            term_matrix = pd.DataFrame.sparse.from_spmatrix(term_matrix)
            term_matrix.columns = vectorizer.get_feature_names_out()
            term_matrix = pd.concat([term_matrix, df[target].reset_index(drop=True)], axis=1)
        else: 
            term_matrix = tokenize(sampled_data)
            vectorizer = Word2Vec(term_matrix['tokens'], **params)
            term_matrix['word2vec_features'] = term_matrix['tokens'].apply(get_word2vec_features, args=(vectorizer,))
            term_matrix = pd.DataFrame(term_matrix['word2vec_features'].tolist())
            term_matrix.columns = term_matrix.columns.astype(str)
            term_matrix.fillna(0, inplace=True)
            score_similarity = evaluate_vectorization(term_matrix.to_numpy())
            term_matrix = pd.concat([term_matrix, df[target].reset_index(drop=True)], axis=1)

        X_train, X_test, y_train, y_test = split(term_matrix, target=target)

        # Run training with predefined parameters and multiple metrics
        best_algorithm, model, score = training_model(X_train, X_test, y_train, y_test, 
                                               algorithms=['rf', 'svm', 'nb', 'knn', 'lr'], verbose=1)

        # Update the best score and parameters if necessary
        if score_similarity < best_similarity:
            best_similarity = score_similarity
            
        if score > best_score:
            best_score = score
            best_params = params
            best_model = model

        # Show progress and estimated time
        elapsed_time = time.time() - start_time
        remaining_time = (elapsed_time / idx) * (total_combinations - idx)
        print(f"Score: {score:.4f} | Best: {best_score:.4f}")
        print(f"Similarity: {score_similarity:.4f} | Best: {best_similarity:.4f}")
        print(f"Elapsed time: {elapsed_time:.2f}s | Remaining time: {remaining_time:.2f}s")
        
        #Saving the results in the DataFrame
        y_pred = model.predict(X_test)
        accuracy = accuracy_score(y_test, y_pred)
        new_data = [df_name, algorithm, params, best_algorithm, accuracy, score, score_similarity]
        df_results.loc[len(df_results)] = new_data

    print("\nBest combination of parameters:", best_params)
    print("Best score:", best_score)
    df_results.to_csv("Results.csv", index=False)

    return best_params, best_score, best_model
    

def treinando(df_name, column, target, algorithm, param_grid):
    inicio_tempo = time.time()
    df = pd.read_csv(f'../datasets/{df_name}')
    df = df[[column,target]].copy()
    display(df.head())
    
    preprocessing_functions = ['transform_to_lowercase', 'remove_special_characters', 'remove_stopwords']
    
    processed_df = preprocess_data(data=df, 
                                   preprocessing_funcs=preprocessing_functions, 
                                   column=column, target=target, verbose=1)
    
    best_params, best_score, best_model = optimize_vectorization(df_name=df_name,
                                                                 df=processed_df, column='prep', target=target, 
                                                                 param_grid=param_grid, algorithm=algorithm)
    
    
    end_time = time.time()
    
    execution_time = end_time - inicio_tempo
    print(f"Execution time: {execution_time} seconds")

# Tests

## Dataset 1 - https://www.kaggle.com/code/hetulmehta/classification-of-websites?select=website_classification.csv

In [12]:
df_name = 'website_classification.csv'
column = 'cleaned_website_text'
target = 'Category'

In [2]:
algorithm = 'tfidf'

param_grid = {
    'max_features': [100, 1000, 5000],
    'ngram_range': [(1, 1), (1, 2), (1, 3)],
    'min_df': [1, 10],
    'max_df': [0.8, 1.0],
    'norm': ['l1', 'l2']
}

treinando(df_name, column, target, algorithm, param_grid)

cleaned_website_text Category
0  official site good hotel accommodation big sav...   Travel
1  expedia hotel book sites like use vacation wor...   Travel
2  tripadvisor hotel book sites like previously d...   Travel
3  cheap flights search compare flights momondo f...   Travel
4  bot create free account create free account si...   Travel

=============================== RUNNING THE PREPROCESSING ===============================

Defined pipeline: ['transform_to_lowercase', 'remove_special_characters', 'remove_stopwords'] 

Preprocess --> transform_to_lowercase
Converting text to lowercase...
Done!

Preprocess --> remove_special_characters
Removing special characters from text...
Done!

Preprocess --> remove_stopwords
Getting stopword list and removing from text...


[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


Done!

=============================== END OF THE PREPROCESSING ================================

O arquivo 'Resultados.csv' existe na pasta, carregando os dados...

Dataset pequeno. Iniciando com tfidf padrão.
Running Bayesian optimization for algorithm rf


BayesSearchCV: 100%|██████████| 32/32 [02:56<00:00,  5.51s/it]


...

Best parameters for nb: OrderedDict([('alpha', 0.03745784902160878)])
Best f1_macro score with nb for test data: 0.8630087624357092

Running Bayesian optimization for algorithm knn


BayesSearchCV: 100%|██████████| 32/32 [00:19<00:00,  1.66it/s]


Best parameters for knn: OrderedDict([('leaf_size', 10), ('n_neighbors', 10)])
Best f1_macro score with knn for test data: 0.8546775908398199

Running Bayesian optimization for algorithm lr


BayesSearchCV: 100%|██████████| 32/32 [02:08<00:00,  4.02s/it]

Best parameters for lr: OrderedDict([('C', 7.443359708150802), ('max_iter', 100)])
Best f1_macro score with lr for test data: 0.8703411994357573

Best algorithm: lr with best f1_macro score: 0.8703411994357573
Best parameters: OrderedDict([('C', 7.443359708150802), ('max_iter', 100)])
Classification Report in the test data:

                                 precision    recall  f1-score   support

                          Adult       0.75      0.50      0.60         6
             Business/Corporate       0.85      0.82      0.84        40
       Computers and Technology       0.70      0.92      0.79        25
                     E-Commerce       0.89      0.92      0.90        36
                      Education       0.93      0.93      0.93        45
                           Food       0.93      0.93      0.93        30
                         Forums       1.00      0.25      0.40         4
                          Games       0.97      0.91      0.94        33
             He

In [4]:
algorithm = 'bow'

param_grid = {
    'max_features': [100, 1000, 5000],
    'ngram_range': [(1, 1), (1, 2), (1, 3)],
    'min_df': [1, 10],
    'max_df': [0.8, 1.0],
    'binary': [True, False]
}

treinando(df_name, column, target, algorithm, param_grid)

cleaned_website_text Category
0  official site good hotel accommodation big sav...   Travel
1  expedia hotel book sites like use vacation wor...   Travel
2  tripadvisor hotel book sites like previously d...   Travel
3  cheap flights search compare flights momondo f...   Travel
4  bot create free account create free account si...   Travel

=============================== RUNNING THE PREPROCESSING ===============================

Defined pipeline: ['transform_to_lowercase', 'remove_special_characters', 'remove_stopwords'] 

Preprocess --> transform_to_lowercase
Converting text to lowercase...
Done!

Preprocess --> remove_special_characters
Removing special characters from text...
Done!

Preprocess --> remove_stopwords
Getting stopword list and removing from text...


[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


Done!

=============================== END OF THE PREPROCESSING ================================

O arquivo 'Resultados.csv' existe na pasta, carregando os dados...

Dataset pequeno. Iniciando com bow padrão.
Running Bayesian optimization for algorithm rf


BayesSearchCV: 100%|██████████| 32/32 [02:31<00:00,  4.73s/it]


...

Best parameters for nb: OrderedDict([('alpha', 0.4861518228524981)])
Best f1_macro score with nb for test data: 0.8616977692925989

Running Bayesian optimization for algorithm knn


BayesSearchCV: 100%|██████████| 32/32 [00:17<00:00,  1.82it/s]


Best parameters for knn: OrderedDict([('leaf_size', 50), ('n_neighbors', 1)])
Best f1_macro score with knn for test data: 0.5641142981312255

Running Bayesian optimization for algorithm lr


BayesSearchCV: 100%|██████████| 32/32 [03:42<00:00,  6.95s/it]

Best parameters for lr: OrderedDict([('C', 0.010469147691862822), ('max_iter', 1000)])
Best f1_macro score with lr for test data: 0.826882366545173

Best algorithm: nb with best f1_macro score: 0.8616977692925989
Best parameters: OrderedDict([('alpha', 0.4861518228524981)])
Classification Report in the test data:

                                 precision    recall  f1-score   support

                          Adult       0.83      0.83      0.83         6
             Business/Corporate       0.71      0.68      0.69        40
       Computers and Technology       0.67      0.88      0.76        25
                     E-Commerce       0.89      0.89      0.89        36
                      Education       0.97      0.80      0.88        45
                           Food       0.96      0.90      0.93        30
                         Forums       0.40      0.50      0.44         4
                          Games       0.97      0.91      0.94        33
             Health and Fi

In [5]:
algorithm = 'word2vec'

param_grid = {
    'vector_size': [100, 1000, 5000],
    'window': [3, 5, 7],
    'min_count': [5, 10],
    'sg': [0, 1],
    'hs': [0, 1],
    'workers': [1]
}

treinando(df_name, column, target, algorithm, param_grid)

cleaned_website_text Category
0  official site good hotel accommodation big sav...   Travel
1  expedia hotel book sites like use vacation wor...   Travel
2  tripadvisor hotel book sites like previously d...   Travel
3  cheap flights search compare flights momondo f...   Travel
4  bot create free account create free account si...   Travel

=============================== RUNNING THE PREPROCESSING ===============================

Defined pipeline: ['transform_to_lowercase', 'remove_special_characters', 'remove_stopwords'] 

Preprocess --> transform_to_lowercase
Converting text to lowercase...
Done!

Preprocess --> remove_special_characters
Removing special characters from text...
Done!

Preprocess --> remove_stopwords
Getting stopword list and removing from text...


[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


Done!

=============================== END OF THE PREPROCESSING ================================

O arquivo 'Resultados.csv' existe na pasta, carregando os dados...

Dataset pequeno. Iniciando com word2vec padrão.
Running Bayesian optimization for algorithm rf


BayesSearchCV: 100%|██████████| 32/32 [00:34<00:00,  1.09s/it]


...

An error occurred with algorithm nb: Negative values in data passed to MultinomialNB (input X)

Running Bayesian optimization for algorithm knn


BayesSearchCV: 100%|██████████| 32/32 [00:15<00:00,  2.04it/s]


Best parameters for knn: OrderedDict([('leaf_size', 10), ('n_neighbors', 1)])
Best f1_macro score with knn for test data: 0.8001449516810879

Running Bayesian optimization for algorithm lr


BayesSearchCV: 100%|██████████| 32/32 [02:02<00:00,  3.82s/it]

Best parameters for lr: OrderedDict([('C', 9.986765764632707), ('max_iter', 141)])
Best f1_macro score with lr for test data: 0.8565284480142242

Best algorithm: lr with best f1_macro score: 0.8565284480142242
Best parameters: OrderedDict([('C', 9.986765764632707), ('max_iter', 141)])
Classification Report in the test data:

                                 precision    recall  f1-score   support

                          Adult       1.00      1.00      1.00         6
             Business/Corporate       0.78      0.72      0.75        40
       Computers and Technology       0.63      0.76      0.69        25
                     E-Commerce       0.91      0.86      0.89        36
                      Education       0.91      0.89      0.90        45
                           Food       0.93      0.90      0.92        30
                         Forums       0.50      0.25      0.33         4
                          Games       0.97      0.88      0.92        33
             He

## Dataset 2 - https://www.kaggle.com/datasets/alfathterry/bbc-full-text-document-classification

In [6]:
df_name = 'document_classification.csv'
column = 'data'
target = 'labels_target'

In [7]:
algorithm = 'tfidf'

param_grid = {
    'max_features': [100, 1000, 5000],
    'ngram_range': [(1, 1), (1, 2), (1, 3)],
    'min_df': [1, 10],
    'max_df': [0.8, 1.0],
    'norm': ['l1', 'l2']
}

treinando(df_name, column, target, algorithm, param_grid)

data  labels_target
0  Musicians to tackle US red tape  Musicians gro...  entertainment
1  U2s desire to be number one  U2, who have won ...  entertainment
2  Rocker Doherty in on-stage fight  Rock singer ...  entertainment
3  Snicket tops US box office chart  The film ada...  entertainment
4  Oceans Twelve raids box office  Oceans Twelve,...  entertainment

=============================== RUNNING THE PREPROCESSING ===============================

Defined pipeline: ['transform_to_lowercase', 'remove_special_characters', 'remove_stopwords'] 

Preprocess --> transform_to_lowercase
Converting text to lowercase...
Done!

Preprocess --> remove_special_characters
Removing special characters from text...
Done!

Preprocess --> remove_stopwords
Getting stopword list and removing from text...


[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


Done!

=============================== END OF THE PREPROCESSING ================================

O arquivo 'Resultados.csv' existe na pasta, carregando os dados...

Dataset pequeno. Iniciando com tfidf padrão.
Running Bayesian optimization for algorithm rf


BayesSearchCV: 100%|██████████| 32/32 [02:11<00:00,  4.11s/it]


...

Best parameters for nb: OrderedDict([('alpha', 0.3516632820656232)])
Best f1_macro score with nb for test data: 0.9797221285407834

Running Bayesian optimization for algorithm knn


BayesSearchCV: 100%|██████████| 32/32 [00:18<00:00,  1.76it/s]


Best parameters for knn: OrderedDict([('leaf_size', 10), ('n_neighbors', 28)])
Best f1_macro score with knn for test data: 0.9521502629334477

Running Bayesian optimization for algorithm lr


BayesSearchCV: 100%|██████████| 32/32 [01:04<00:00,  2.02s/it]

Best parameters for lr: OrderedDict([('C', 2.9724392943261897), ('max_iter', 1000)])
Best f1_macro score with lr for test data: 0.9789814789074013

Best algorithm: nb with best f1_macro score: 0.9797221285407834
Best parameters: OrderedDict([('alpha', 0.3516632820656232)])
Classification Report in the test data:

               precision    recall  f1-score   support

     business       0.96      0.97      0.97       179
entertainment       0.99      0.98      0.99       135
     politics       0.98      0.98      0.98       126
        sport       1.00      1.00      1.00       160
         tech       0.96      0.97      0.97       135

     accuracy                           0.98       735
    macro avg       0.98      0.98      0.98       735
 weighted avg       0.98      0.98      0.98       735

Score: 0.9797 | Melhor até agora: 0.9809
Similarity: 0.0359 | Melhor até agora: 0.0242
Tempo decorrido: 16325.18s | Tempo estimado restante: 0.00s

Melhor combinação de parâmetros: {'max_

In [8]:
algorithm = 'bow'

param_grid = {
    'max_features': [100, 1000, 5000],
    'ngram_range': [(1, 1), (1, 2), (1, 3)],
    'min_df': [1, 10],
    'max_df': [0.8, 1.0],
    'binary': [True, False]
}

treinando(df_name, column, target, algorithm, param_grid)

data  labels_target
0  Musicians to tackle US red tape  Musicians gro...  entertainment
1  U2s desire to be number one  U2, who have won ...  entertainment
2  Rocker Doherty in on-stage fight  Rock singer ...  entertainment
3  Snicket tops US box office chart  The film ada...  entertainment
4  Oceans Twelve raids box office  Oceans Twelve,...  entertainment

=============================== RUNNING THE PREPROCESSING ===============================

Defined pipeline: ['transform_to_lowercase', 'remove_special_characters', 'remove_stopwords'] 

Preprocess --> transform_to_lowercase
Converting text to lowercase...
Done!

Preprocess --> remove_special_characters
Removing special characters from text...
Done!

Preprocess --> remove_stopwords
Getting stopword list and removing from text...


[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


Done!

=============================== END OF THE PREPROCESSING ================================

O arquivo 'Resultados.csv' existe na pasta, carregando os dados...

Dataset pequeno. Iniciando com bow padrão.
Running Bayesian optimization for algorithm rf


BayesSearchCV: 100%|██████████| 32/32 [02:12<00:00,  4.15s/it]


...

Best parameters for nb: OrderedDict([('alpha', 0.02970460012806774)])
Best f1_macro score with nb for test data: 0.9755829044731203

Running Bayesian optimization for algorithm knn


BayesSearchCV: 100%|██████████| 32/32 [00:20<00:00,  1.55it/s]


Best parameters for knn: OrderedDict([('leaf_size', 50), ('n_neighbors', 1)])
Best f1_macro score with knn for test data: 0.8021300364997715

Running Bayesian optimization for algorithm lr


BayesSearchCV: 100%|██████████| 32/32 [01:11<00:00,  2.22s/it]

Best parameters for lr: OrderedDict([('C', 2.0496137473886704), ('max_iter', 118)])
Best f1_macro score with lr for test data: 0.971928907293482

Best algorithm: nb with best f1_macro score: 0.9755829044731203
Best parameters: OrderedDict([('alpha', 0.02970460012806774)])
Classification Report in the test data:

               precision    recall  f1-score   support

     business       0.97      0.96      0.96       179
entertainment       0.99      0.97      0.98       135
     politics       0.98      0.98      0.98       126
        sport       1.00      0.99      1.00       160
         tech       0.94      0.98      0.96       135

     accuracy                           0.98       735
    macro avg       0.98      0.98      0.98       735
 weighted avg       0.98      0.98      0.98       735

Score: 0.9756 | Melhor até agora: 0.9837
Similarity: 0.0877 | Melhor até agora: 0.0642
Tempo decorrido: 15635.28s | Tempo estimado restante: 0.00s

Melhor combinação de parâmetros: {'analy

In [9]:
algorithm = 'word2vec'

param_grid = {
    'vector_size': [100, 1000, 5000],
    'window': [3, 5, 7],
    'min_count': [5, 10],
    'sg': [0, 1],
    'hs': [0, 1],
    'workers': [1]
}

treinando(df_name, column, target, algorithm, param_grid)

data  labels_target
0  Musicians to tackle US red tape  Musicians gro...  entertainment
1  U2s desire to be number one  U2, who have won ...  entertainment
2  Rocker Doherty in on-stage fight  Rock singer ...  entertainment
3  Snicket tops US box office chart  The film ada...  entertainment
4  Oceans Twelve raids box office  Oceans Twelve,...  entertainment

=============================== RUNNING THE PREPROCESSING ===============================

Defined pipeline: ['transform_to_lowercase', 'remove_special_characters', 'remove_stopwords'] 

Preprocess --> transform_to_lowercase
Converting text to lowercase...
Done!

Preprocess --> remove_special_characters
Removing special characters from text...
Done!

Preprocess --> remove_stopwords
Getting stopword list and removing from text...


[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


Done!

=============================== END OF THE PREPROCESSING ================================

O arquivo 'Resultados.csv' existe na pasta, carregando os dados...

Dataset pequeno. Iniciando com word2vec padrão.
Running Bayesian optimization for algorithm rf


BayesSearchCV: 100%|██████████| 32/32 [00:45<00:00,  1.41s/it]


...

An error occurred with algorithm nb: Negative values in data passed to MultinomialNB (input X)

Running Bayesian optimization for algorithm knn


BayesSearchCV: 100%|██████████| 32/32 [00:21<00:00,  1.50it/s]


Best parameters for knn: OrderedDict([('leaf_size', 10), ('n_neighbors', 17)])
Best f1_macro score with knn for test data: 0.9569923885900316

Running Bayesian optimization for algorithm lr


BayesSearchCV: 100%|██████████| 32/32 [01:14<00:00,  2.32s/it]


Best parameters for lr: OrderedDict([('C', 7.795275297424463), ('max_iter', 100)])
Best f1_macro score with lr for test data: 0.9727227002570341

Best algorithm: svm with best f1_macro score: 0.9794559521059145
Best parameters: OrderedDict([('C', 1.8494150749249993), ('gamma', 1.0635297246368989)])
Classification Report in the test data:

               precision    recall  f1-score   support

     business       0.96      0.98      0.97       179
entertainment       0.99      0.99      0.99       135
     politics       0.96      0.97      0.96       126
        sport       1.00      0.99      1.00       160
         tech       0.99      0.97      0.98       135

     accuracy                           0.98       735
    macro avg       0.98      0.98      0.98       735
 weighted avg       0.98      0.98      0.98       735

Score: 0.9795 | Melhor até agora: 0.9797
Similarity: 0.6756 | Melhor até agora: 0.5373
Tempo decorrido: 23538.19s | Tempo estimado restante: 0.00s

Melhor combin

## Dataset 3 - https://www.kaggle.com/code/abhishek0032/mastering-email-spam-detection-eda-insights/input?select=train.csv

In [2]:
df_name = 'spam_or_ham.csv'
column = 'sms'
target = 'label'

In [11]:
algorithm = 'tfidf'

param_grid = {
    'max_features': [100, 1000, 5000],
    'ngram_range': [(1, 1), (1, 2), (1, 3)],
    'min_df': [1, 10],
    'max_df': [0.8, 1.0],
    'norm': ['l1', 'l2']
}

treinando(df_name, column, target, algorithm, param_grid)

sms  label
0  Go until jurong point, crazy.. Available only ...      0
1                    Ok lar... Joking wif u oni...\n      0
2  Free entry in 2 a wkly comp to win FA Cup fina...      1
3  U dun say so early hor... U c already then say...      0
4  Nah I don't think he goes to usf, he lives aro...      0

=============================== RUNNING THE PREPROCESSING ===============================

Defined pipeline: ['transform_to_lowercase', 'remove_special_characters', 'remove_stopwords'] 

Preprocess --> transform_to_lowercase
Converting text to lowercase...
Done!

Preprocess --> remove_special_characters
Removing special characters from text...
Done!

Preprocess --> remove_stopwords
Getting stopword list and removing from text...


[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


Done!

=============================== END OF THE PREPROCESSING ================================

O arquivo 'Resultados.csv' existe na pasta, carregando os dados...

Dataset pequeno. Iniciando com tfidf padrão.
Running Bayesian optimization for algorithm rf


BayesSearchCV: 100%|██████████| 32/32 [03:29<00:00,  6.56s/it]


...

Best parameters for nb: OrderedDict([('alpha', 0.020871588778809444)])
Best f1_macro score with nb for test data: 0.965797914970262

Running Bayesian optimization for algorithm knn


BayesSearchCV: 100%|██████████| 32/32 [00:17<00:00,  1.84it/s]


Best parameters for knn: OrderedDict([('leaf_size', 50), ('n_neighbors', 1)])
Best f1_macro score with knn for test data: 0.8991058143734201

Running Bayesian optimization for algorithm lr


BayesSearchCV: 100%|██████████| 32/32 [00:17<00:00,  1.78it/s]


Best parameters for lr: OrderedDict([('C', 10.0), ('max_iter', 100)])
Best f1_macro score with lr for test data: 0.9686265756302521

Best algorithm: svm with best f1_macro score: 0.9708309528343808
Best parameters: OrderedDict([('C', 10.0), ('gamma', 0.4841098534374222)])
Classification Report in the test data:

              precision    recall  f1-score   support

           0       0.99      1.00      0.99      1592
           1       0.99      0.91      0.95       246

    accuracy                           0.99      1838
   macro avg       0.99      0.95      0.97      1838
weighted avg       0.99      0.99      0.99      1838

Score: 0.9708 | Melhor até agora: 0.9750
Similarity: 0.0105 | Melhor até agora: 0.0067
Tempo decorrido: 21966.10s | Tempo estimado restante: 0.00s

Melhor combinação de parâmetros: {'max_df': 0.8, 'max_features': 5000, 'min_df': 10, 'ngram_range': (1, 2), 'norm': 'l1'}
Melhor avaliação: 0.9749724260951266
Tempo de execução: 23779.5433678627 segundos


In [12]:
algorithm = 'bow'

param_grid = {
    'max_features': [100, 1000, 5000],
    'ngram_range': [(1, 1), (1, 2), (1, 3)],
    'min_df': [1, 10],
    'max_df': [0.8, 1.0],
    'binary': [True, False]
}

treinando(df_name, column, target, algorithm, param_grid)

sms  label
0  Go until jurong point, crazy.. Available only ...      0
1                    Ok lar... Joking wif u oni...\n      0
2  Free entry in 2 a wkly comp to win FA Cup fina...      1
3  U dun say so early hor... U c already then say...      0
4  Nah I don't think he goes to usf, he lives aro...      0

=============================== RUNNING THE PREPROCESSING ===============================

Defined pipeline: ['transform_to_lowercase', 'remove_special_characters', 'remove_stopwords'] 

Preprocess --> transform_to_lowercase
Converting text to lowercase...
Done!

Preprocess --> remove_special_characters
Removing special characters from text...
Done!

Preprocess --> remove_stopwords
Getting stopword list and removing from text...
Done!



[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


=============================== END OF THE PREPROCESSING ================================

O arquivo 'Resultados.csv' existe na pasta, carregando os dados...

Dataset pequeno. Iniciando com bow padrão.
Running Bayesian optimization for algorithm rf


BayesSearchCV: 100%|██████████| 32/32 [03:16<00:00,  6.13s/it]


...

Best parameters for nb: OrderedDict([('alpha', 1.784148756503194)])
Best f1_macro score with nb for test data: 0.9592838566472759

Running Bayesian optimization for algorithm knn


BayesSearchCV: 100%|██████████| 32/32 [00:25<00:00,  1.27it/s]


Best parameters for knn: OrderedDict([('leaf_size', 50), ('n_neighbors', 1)])
Best f1_macro score with knn for test data: 0.8800677504893861

Running Bayesian optimization for algorithm lr


BayesSearchCV: 100%|██████████| 32/32 [00:18<00:00,  1.75it/s]


Best parameters for lr: OrderedDict([('C', 7.13694615476664), ('max_iter', 1000)])
Best f1_macro score with lr for test data: 0.9648176029475537

Best algorithm: svm with best f1_macro score: 0.9695605658621249
Best parameters: OrderedDict([('C', 4.8791694844275515), ('gamma', 0.08023246075377977)])
Classification Report in the test data:

              precision    recall  f1-score   support

           0       0.99      1.00      0.99      1592
           1       0.99      0.91      0.95       246

    accuracy                           0.99      1838
   macro avg       0.99      0.95      0.97      1838
weighted avg       0.99      0.99      0.99      1838

Score: 0.9696 | Melhor até agora: 0.9696
Similarity: 0.0140 | Melhor até agora: 0.0105
Tempo decorrido: 22008.88s | Tempo estimado restante: 0.00s

Melhor combinação de parâmetros: {'binary': False, 'max_df': 0.8, 'max_features': 1000, 'min_df': 10, 'ngram_range': (1, 3)}
Melhor avaliação: 0.9695605658621249
Tempo de execução: 23

In [3]:
algorithm = 'word2vec'

param_grid = {
    'vector_size': [100, 1000, 5000],
    'window': [3, 5, 7],
    'min_count': [5, 10],
    'sg': [0, 1],
    'hs': [0, 1],
    'workers': [1]
}

treinando(df_name, column, target, algorithm, param_grid)

sms  label
0  Go until jurong point, crazy.. Available only ...      0
1                    Ok lar... Joking wif u oni...\n      0
2  Free entry in 2 a wkly comp to win FA Cup fina...      1
3  U dun say so early hor... U c already then say...      0
4  Nah I don't think he goes to usf, he lives aro...      0

=============================== RUNNING THE PREPROCESSING ===============================

Defined pipeline: ['transform_to_lowercase', 'remove_special_characters', 'remove_stopwords'] 

Preprocess --> transform_to_lowercase
Converting text to lowercase...
Done!

Preprocess --> remove_special_characters
Removing special characters from text...
Done!

Preprocess --> remove_stopwords
Getting stopword list and removing from text...
Done!

=============================== END OF THE PREPROCESSING ================================

O arquivo 'Resultados.csv' existe na pasta, carregando os dados...

Dataset pequeno. Iniciando com word2vec padrão.


[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


Running Bayesian optimization for algorithm rf


BayesSearchCV: 100%|██████████| 32/32 [01:14<00:00,  2.33s/it]


...

An error occurred with algorithm nb: Negative values in data passed to MultinomialNB (input X)

Running Bayesian optimization for algorithm knn


BayesSearchCV: 100%|██████████| 32/32 [00:30<00:00,  1.06it/s]


Best parameters for knn: OrderedDict([('leaf_size', 50), ('n_neighbors', 4)])
Best f1_macro score with knn for test data: 0.9489007003470142

Running Bayesian optimization for algorithm lr


BayesSearchCV: 100%|██████████| 32/32 [00:32<00:00,  1.01s/it]

Best parameters for lr: OrderedDict([('C', 1.5737226686497339), ('max_iter', 108)])
Best f1_macro score with lr for test data: 0.9394314550911552

Best algorithm: rf with best f1_macro score: 0.9635652098846745
Best parameters: OrderedDict([('max_depth', 21), ('n_estimators', 75)])
Classification Report in the test data:

              precision    recall  f1-score   support

           0       0.99      0.99      0.99      1592
           1       0.94      0.93      0.94       246

    accuracy                           0.98      1838
   macro avg       0.96      0.96      0.96      1838
weighted avg       0.98      0.98      0.98      1838

Score: 0.9636 | Melhor até agora: 0.9671
Similarity: 0.6636 | Melhor até agora: 0.6083
Tempo decorrido: 30158.17s | Tempo estimado restante: 0.00s

Melhor combinação de parâmetros: {'hs': 1, 'min_count': 5, 'sg': 1, 'vector_size': 100, 'window': 3, 'workers': 1}
Melhor avaliação: 0.9671477305225313
Tempo de execução: 30271.24093437195 segundos


## Dataset 4 - https://www.kaggle.com/datasets/farwarizvi/emotions-6000?select=train_sam_shuffle.csv

In [2]:
df_name = 'emotions-6000.csv'
column = 'sentence'
target = 'label'

In [3]:
algorithm = 'tfidf'

param_grid = {
    'max_features': [100, 1000, 5000],
    'ngram_range': [(1, 1), (1, 2), (1, 3)],
    'min_df': [1, 10],
    'max_df': [0.8, 1.0],
    'norm': ['l1', 'l2']
}

treinando(df_name, column, target, algorithm, param_grid)

sentence    label
0                 Getting lost in a captivating book      joy
1  No matter how hard I try I can t seem to shake...  sadness
2  His anger was like a ticking time bomb, and he...    anger
3  Their patience and understanding during challe...     love
4     I am scared that my anxiety will never improve     fear

=============================== RUNNING THE PREPROCESSING ===============================

Defined pipeline: ['transform_to_lowercase', 'remove_special_characters', 'remove_stopwords'] 

Preprocess --> transform_to_lowercase
Converting text to lowercase...
Done!

Preprocess --> remove_special_characters
Removing special characters from text...
Done!

Preprocess --> remove_stopwords
Getting stopword list and removing from text...
Done!

=============================== END OF THE PREPROCESSING ================================

O arquivo 'Resultados.csv' existe na pasta, carregando os dados...

Dataset pequeno. Iniciando com tfidf padrão.


[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


Running Bayesian optimization for algorithm rf


BayesSearchCV: 100%|██████████| 32/32 [00:59<00:00,  1.87s/it]


...

Best parameters for nb: OrderedDict([('alpha', 0.4861518228524981)])
Best f1_macro score with nb for test data: 0.8961669329905355

Running Bayesian optimization for algorithm knn


BayesSearchCV: 100%|██████████| 32/32 [00:15<00:00,  2.10it/s]


Best parameters for knn: OrderedDict([('leaf_size', 10), ('n_neighbors', 1)])
Best f1_macro score with knn for test data: 0.8217425136376938

Running Bayesian optimization for algorithm lr


BayesSearchCV: 100%|██████████| 32/32 [00:22<00:00,  1.41it/s]


Best parameters for lr: OrderedDict([('C', 5.156032752922221), ('max_iter', 100)])
Best f1_macro score with lr for test data: 0.9281561830893246

Best algorithm: lr with best f1_macro score: 0.9281561830893246
Best parameters: OrderedDict([('C', 5.156032752922221), ('max_iter', 100)])
Classification Report in the test data:

              precision    recall  f1-score   support

       anger       0.98      0.96      0.97       252
        fear       0.96      0.96      0.96       221
         joy       0.82      0.88      0.85       244
        love       0.93      0.91      0.92       231
     neutral       0.93      0.92      0.92       218
     sadness       0.95      0.94      0.94       221

    accuracy                           0.93      1387
   macro avg       0.93      0.93      0.93      1387
weighted avg       0.93      0.93      0.93      1387

Score: 0.9282 | Melhor até agora: 0.9527
Similarity: 0.0110 | Melhor até agora: 0.0054
Tempo decorrido: 25249.87s | Tempo estimado

In [4]:
algorithm = 'bow'

param_grid = {
    'max_features': [100, 1000, 5000],
    'ngram_range': [(1, 1), (1, 2), (1, 3)],
    'min_df': [1, 10],
    'max_df': [0.8, 1.0],
    'binary': [True, False]
}

treinando(df_name, column, target, algorithm, param_grid)

sentence    label
0                 Getting lost in a captivating book      joy
1  No matter how hard I try I can t seem to shake...  sadness
2  His anger was like a ticking time bomb, and he...    anger
3  Their patience and understanding during challe...     love
4     I am scared that my anxiety will never improve     fear

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


=============================== RUNNING THE PREPROCESSING ===============================

Defined pipeline: ['transform_to_lowercase', 'remove_special_characters', 'remove_stopwords'] 

Preprocess --> transform_to_lowercase
Converting text to lowercase...
Done!

Preprocess --> remove_special_characters
Removing special characters from text...
Done!

Preprocess --> remove_stopwords
Getting stopword list and removing from text...
Done!

=============================== END OF THE PREPROCESSING ================================

O arquivo 'Resultados.csv' existe na pasta, carregando os dados...

Dataset pequeno. Iniciando com bow padrão.
Running Bayesian optimization for algorithm rf


BayesSearchCV: 100%|██████████| 32/32 [00:57<00:00,  1.80s/it]


Best parameters for rf: OrderedDict([('max_depth', 50), ('n_estimators', 100)])
Best f1_macro score with rf for test data: 0.8769384300299546

Running Bayesian optimization for algorithm svm


...

Best parameters for nb: OrderedDict([('alpha', 0.09191900763834451)])
Best f1_macro score with nb for test data: 0.8999547359718706

Running Bayesian optimization for algorithm knn


BayesSearchCV: 100%|██████████| 32/32 [00:22<00:00,  1.43it/s]


Best parameters for knn: OrderedDict([('leaf_size', 50), ('n_neighbors', 1)])
Best f1_macro score with knn for test data: 0.7874325520735598

Running Bayesian optimization for algorithm lr


BayesSearchCV: 100%|██████████| 32/32 [00:31<00:00,  1.02it/s]

Best parameters for lr: OrderedDict([('C', 4.192274779806119), ('max_iter', 104)])
Best f1_macro score with lr for test data: 0.9169462280904508

Best algorithm: lr with best f1_macro score: 0.9169462280904508
Best parameters: OrderedDict([('C', 4.192274779806119), ('max_iter', 104)])
Classification Report in the test data:

              precision    recall  f1-score   support

       anger       0.98      0.94      0.96       252
        fear       0.95      0.93      0.94       221
         joy       0.80      0.86      0.83       244
        love       0.91      0.91      0.91       231
     neutral       0.92      0.91      0.92       218
     sadness       0.95      0.94      0.94       221

    accuracy                           0.92      1387
   macro avg       0.92      0.92      0.92      1387
weighted avg       0.92      0.92      0.92      1387

Score: 0.9169 | Melhor até agora: 0.9421
Similarity: 0.0150 | Melhor até agora: 0.0092
Tempo decorrido: 25122.11s | Tempo estimado

In [3]:
algorithm = 'word2vec'

param_grid = {
    'vector_size': [100, 1000, 5000],
    'window': [3, 5, 7],
    'min_count': [5, 10],
    'sg': [0, 1],
    'hs': [0, 1],
    'workers': [1]
}

treinando(df_name, column, target, algorithm, param_grid)

sentence    label
0                 Getting lost in a captivating book      joy
1  No matter how hard I try I can t seem to shake...  sadness
2  His anger was like a ticking time bomb, and he...    anger
3  Their patience and understanding during challe...     love
4     I am scared that my anxiety will never improve     fear

=============================== RUNNING THE PREPROCESSING ===============================

Defined pipeline: ['transform_to_lowercase', 'remove_special_characters', 'remove_stopwords'] 

Preprocess --> transform_to_lowercase
Converting text to lowercase...
Done!

Preprocess --> remove_special_characters
Removing special characters from text...
Done!

Preprocess --> remove_stopwords
Getting stopword list and removing from text...
Done!

=============================== END OF THE PREPROCESSING ================================

O arquivo 'Resultados.csv' existe na pasta, carregando os dados...

Dataset pequeno. Iniciando com word2vec padrão.


[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


Running Bayesian optimization for algorithm rf


BayesSearchCV: 100%|██████████| 32/32 [01:30<00:00,  2.82s/it]


...

An error occurred with algorithm nb: Negative values in data passed to MultinomialNB (input X)

Running Bayesian optimization for algorithm knn


BayesSearchCV: 100%|██████████| 32/32 [00:22<00:00,  1.40it/s]


Best parameters for knn: OrderedDict([('leaf_size', 10), ('n_neighbors', 1)])
Best f1_macro score with knn for test data: 0.7937088238752076

Running Bayesian optimization for algorithm lr


BayesSearchCV: 100%|██████████| 32/32 [03:58<00:00,  7.45s/it]


Best parameters for lr: OrderedDict([('C', 9.986765764632707), ('max_iter', 141)])
Best f1_macro score with lr for test data: 0.7733191736269087

Best algorithm: svm with best f1_macro score: 0.8366449105705288
Best parameters: OrderedDict([('C', 7.431757970106022), ('gamma', 10.0)])
Classification Report in the test data:

              precision    recall  f1-score   support

       anger       0.91      0.85      0.88       252
        fear       0.87      0.87      0.87       221
         joy       0.73      0.74      0.73       244
        love       0.84      0.83      0.83       231
     neutral       0.85      0.87      0.86       218
     sadness       0.83      0.86      0.84       221

    accuracy                           0.84      1387
   macro avg       0.84      0.84      0.84      1387
weighted avg       0.84      0.84      0.84      1387

Score: 0.8366 | Melhor até agora: 0.8947
Similarity: 0.8358 | Melhor até agora: 0.6579
Tempo decorrido: 57527.48s | Tempo estimado 

## Dataset 5 - https://www.kaggle.com/datasets/mohidabdulrehman/vs-sentiment-analysis

In [3]:
df_name = 'sentiment_reviews_dataset.csv'
column = 'sentence'
target = 'label'

In [7]:
algorithm = 'tfidf'

param_grid = {
    'max_features': [100, 1000, 5000],
    'ngram_range': [(1, 1), (1, 2), (1, 3)],
    'min_df': [1, 10],
    'max_df': [0.8, 1.0],
    'norm': ['l1', 'l2']
}

treinando(df_name, column, target, algorithm, param_grid)

sentence  label
0                           Wow... Loved this place.      1
1                                 Crust is not good.      0
2          Not tasty and the texture was just nasty.      0
3  Stopped by during the late May bank holiday of...      1
4  The selection on the menu was great and so wer...      1

=============================== RUNNING THE PREPROCESSING ===============================

Defined pipeline: ['transform_to_lowercase', 'remove_special_characters', 'remove_stopwords'] 

Preprocess --> transform_to_lowercase
Converting text to lowercase...
Done!

Preprocess --> remove_special_characters
Removing special characters from text...
Done!

Preprocess --> remove_stopwords
Getting stopword list and removing from text...
Done!

=============================== END OF THE PREPROCESSING ================================

O arquivo 'Resultados.csv' existe na pasta, carregando os dados...

Dataset pequeno. Iniciando com tfidf padrão.


[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


Running Bayesian optimization for algorithm rf


BayesSearchCV: 100%|██████████| 32/32 [00:24<00:00,  1.28it/s]


...

Best parameters for nb: OrderedDict([('alpha', 0.0007425534359037013)])
Best f1_macro score with nb for test data: 0.6515119514412437

Running Bayesian optimization for algorithm knn


BayesSearchCV: 100%|██████████| 32/32 [00:15<00:00,  2.06it/s]


Best parameters for knn: OrderedDict([('leaf_size', 10), ('n_neighbors', 3)])
Best f1_macro score with knn for test data: 0.6893866646383784

Running Bayesian optimization for algorithm lr


BayesSearchCV: 100%|██████████| 32/32 [00:16<00:00,  1.97it/s]

Best parameters for lr: OrderedDict([('C', 1.74010727088096), ('max_iter', 1000)])
Best f1_macro score with lr for test data: 0.7225974025974027

Best algorithm: lr with best f1_macro score: 0.7225974025974027
Best parameters: OrderedDict([('C', 1.74010727088096), ('max_iter', 1000)])
Classification Report in the test data:

              precision    recall  f1-score   support

           0       0.71      0.84      0.77       177
           1       0.76      0.61      0.68       153

    accuracy                           0.73       330
   macro avg       0.74      0.72      0.72       330
weighted avg       0.74      0.73      0.73       330

Score: 0.7226 | Melhor até agora: 0.7850
Similarity: 0.0263 | Melhor até agora: 0.0063
Tempo decorrido: 7114.98s | Tempo estimado restante: 0.00s

Melhor combinação de parâmetros: {'max_df': 0.8, 'max_features': 1000, 'min_df': 1, 'ngram_range': (1, 3), 'norm': 'l1'}
Melhor avaliação: 0.785028290649196
Tempo de execução: 7205.261463403702 segun

In [4]:
algorithm = 'bow'

param_grid = {
    'max_features': [100, 1000, 5000],
    'ngram_range': [(1, 1), (1, 2), (1, 3)],
    'min_df': [1, 10],
    'max_df': [0.8, 1.0],
    'binary': [True, False]
}

treinando(df_name, column, target, algorithm, param_grid)

sentence  label
0                           Wow... Loved this place.      1
1                                 Crust is not good.      0
2          Not tasty and the texture was just nasty.      0
3  Stopped by during the late May bank holiday of...      1
4  The selection on the menu was great and so wer...      1

=============================== RUNNING THE PREPROCESSING ===============================

Defined pipeline: ['transform_to_lowercase', 'remove_special_characters', 'remove_stopwords'] 

Preprocess --> transform_to_lowercase
Converting text to lowercase...
Done!

Preprocess --> remove_special_characters
Removing special characters from text...
Done!

Preprocess --> remove_stopwords
Getting stopword list and removing from text...
Done!

=============================== END OF THE PREPROCESSING ================================

O arquivo 'Resultados.csv' existe na pasta, carregando os dados...

Dataset pequeno. Iniciando com bow padrão.


[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


Running Bayesian optimization for algorithm rf


BayesSearchCV: 100%|██████████| 32/32 [00:25<00:00,  1.24it/s]


...

Best parameters for nb: OrderedDict([('alpha', 0.395252013727049)])
Best f1_macro score with nb for test data: 0.6664706530927267

Running Bayesian optimization for algorithm knn


BayesSearchCV: 100%|██████████| 32/32 [00:17<00:00,  1.79it/s]


Best parameters for knn: OrderedDict([('leaf_size', 10), ('n_neighbors', 1)])
Best f1_macro score with knn for test data: 0.6963545470930288

Running Bayesian optimization for algorithm lr


BayesSearchCV: 100%|██████████| 32/32 [00:18<00:00,  1.70it/s]

Best parameters for lr: OrderedDict([('C', 0.6812046788520796), ('max_iter', 1000)])
Best f1_macro score with lr for test data: 0.7333117827703248

Best algorithm: lr with best f1_macro score: 0.7333117827703248
Best parameters: OrderedDict([('C', 0.6812046788520796), ('max_iter', 1000)])
Classification Report in the test data:

              precision    recall  f1-score   support

           0       0.71      0.86      0.78       177
           1       0.79      0.60      0.68       153

    accuracy                           0.74       330
   macro avg       0.75      0.73      0.73       330
weighted avg       0.75      0.74      0.74       330

Score: 0.7333 | Melhor até agora: 0.7960
Similarity: 0.0312 | Melhor até agora: 0.0117
Tempo decorrido: 7373.47s | Tempo estimado restante: 0.00s

Melhor combinação de parâmetros: {'binary': False, 'max_df': 0.8, 'max_features': 5000, 'min_df': 1, 'ngram_range': (1, 2)}
Melhor avaliação: 0.7960368594545999
Tempo de execução: 7469.3294315338

In [5]:
algorithm = 'word2vec'

param_grid = {
    'vector_size': [100, 1000, 5000],
    'window': [3, 5, 7],
    'min_count': [5, 10],
    'sg': [0, 1],
    'hs': [0, 1],
    'workers': [1]
}

treinando(df_name, column, target, algorithm, param_grid)

sentence  label
0                           Wow... Loved this place.      1
1                                 Crust is not good.      0
2          Not tasty and the texture was just nasty.      0
3  Stopped by during the late May bank holiday of...      1
4  The selection on the menu was great and so wer...      1

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


=============================== RUNNING THE PREPROCESSING ===============================

Defined pipeline: ['transform_to_lowercase', 'remove_special_characters', 'remove_stopwords'] 

Preprocess --> transform_to_lowercase
Converting text to lowercase...
Done!

Preprocess --> remove_special_characters
Removing special characters from text...
Done!

Preprocess --> remove_stopwords
Getting stopword list and removing from text...
Done!

=============================== END OF THE PREPROCESSING ================================

O arquivo 'Resultados.csv' existe na pasta, carregando os dados...

Dataset pequeno. Iniciando com word2vec padrão.
Running Bayesian optimization for algorithm rf


BayesSearchCV: 100%|██████████| 32/32 [00:31<00:00,  1.01it/s]


Best parameters for rf: OrderedDict([('max_depth', 48), ('n_estimators', 73)])
Best f1_macro score with rf for test data: 0.6674709487755498

Running Bayesian optimization for algorithm svm


...

An error occurred with algorithm nb: Negative values in data passed to MultinomialNB (input X)

Running Bayesian optimization for algorithm knn


BayesSearchCV: 100%|██████████| 32/32 [00:16<00:00,  1.91it/s]


Best parameters for knn: OrderedDict([('leaf_size', 50), ('n_neighbors', 3)])
Best f1_macro score with knn for test data: 0.6801491146318732

Running Bayesian optimization for algorithm lr


BayesSearchCV: 100%|██████████| 32/32 [00:14<00:00,  2.16it/s]

Best parameters for lr: OrderedDict([('C', 0.0007425534359037013), ('max_iter', 755)])
Best f1_macro score with lr for test data: 0.3167701863354037

Best algorithm: rf with best f1_macro score: 0.6924510717614165
Best parameters: OrderedDict([('max_depth', 36), ('n_estimators', 99)])
Classification Report in the test data:

              precision    recall  f1-score   support

           0       0.70      0.76      0.73       177
           1       0.69      0.62      0.66       153

    accuracy                           0.70       330
   macro avg       0.70      0.69      0.69       330
weighted avg       0.70      0.70      0.70       330

Score: 0.6925 | Melhor até agora: 0.7326
Similarity: 0.1104 | Melhor até agora: 0.0531
Tempo decorrido: 8403.87s | Tempo estimado restante: 0.00s

Melhor combinação de parâmetros: {'hs': 0, 'min_count': 5, 'sg': 0, 'vector_size': 1000, 'window': 7, 'workers': 1}
Melhor avaliação: 0.7326292850557372
Tempo de execução: 8463.674839258194 segundos
